In [1]:
import xarray as xr
import hvplot.xarray

In [2]:
zarr_ds = '/caldera/projects/usgs/hazards/cmgp/woodshole/rsignell/EarthMap/Projects/de_bay/zarr_001'
ds = xr.open_zarr(zarr_ds, consolidated=True)

In [21]:
a = ds.indexes['ocean_time'].duplicated()

In [24]:
import numpy as np
b = np.where(a==False)

In [25]:
len(b)

1

In [7]:
ds.drop_sel(ocean_time=a)

InvalidIndexError: Reindexing only valid with uniquely valued Index objects

In [6]:
from dask.distributed import Client
from dask_jobqueue import SLURMCluster
cluster = SLURMCluster(processes=1, cores=1, memory='8GB', interface='ipogif0',
                       project='woodshole', walltime='01:00:00')

In [7]:
client = Client(cluster)
print(cluster.job_script())

#!/usr/bin/env bash

#SBATCH -J dask-worker
#SBATCH -A woodshole
#SBATCH -n 1
#SBATCH --cpus-per-task=1
#SBATCH --mem=8G
#SBATCH -t 01:00:00

/home/rsignell/miniconda3/envs/pangeo3/bin/python -m distributed.cli.dask_worker tcp://10.128.0.39:39567 --nthreads 1 --memory-limit 8.00GB --name name --nanny --death-timeout 60 --interface ipogif0



In [8]:
cluster.scale(20)

In [9]:
cluster

In [10]:
s1 = ds.salt[:,-1,40,50].load()

In [13]:
s1.hvplot(grid=True)

:Curve   [ocean_time]   (salt)

In [17]:
%%time
smax = ds.salt.max(dim='ocean_time').compute()

CPU times: user 22.5 s, sys: 996 ms, total: 23.5 s
Wall time: 33.3 s


In [21]:
smax[-1,:,:].hvplot.quadmesh(x='lon_rho',y='lat_rho', 
            geo=True, tiles='OSM', rasterize=True, 
            cmap='rainbow', frame_width=300, clim=(0,5))

:DynamicMap   []
   :Overlay
      .Tiles.I :Tiles   [x,y]
      .Image.I :Image   [lon_rho,lat_rho]   (salt)

In [ ]:
cluster.close()